In [1]:
# modified from https://github.com/SherlockLiao/Deep-Dream/blob/master/show_image.ipynb
import torch
import torchvision.models as models
from torchvision import transforms
from PIL import Image
from deepDream import dream
import torch.nn as nn
import spectroUtils as sUtils
import IPython.display as ipd
import librosa
import librosa.display
import numpy as np
import math
from torch.autograd import Variable

('track', 'tags')
('album', 'tags')
('artist', 'tags')
('track', 'genres')
('track', 'genres_all')


/home/iaakhter/cs532l/DreamingInMusic/utils.py:218: FutureWarning: specifying 'categories' or 'ordered' in .astype() is deprecated; pass a CategoricalDtype instead
  'category', categories=SUBSETS, ordered=True)


In [2]:
#Original hip-hopaudio
trackId = 2
minAmp = -80.0
maxAmp = 1.9073486e-06
audioDirectory = "data/fma_small/"
audioFilename = audioDirectory + "000/000002.mp3"
x, sr = librosa.load(audioFilename, sr=None, mono=True, duration = 10, offset = 0)
start, end = 0, 30
ipd.Audio(data=x[start*sr:end*sr], rate=sr)

In [3]:
#scaledSpectro, phase, origSpectroSize = sUtils.loadSpectro(trackId, spectroSize, minAmp, maxAmp)
#scaledSpectro = scaledSpectro.data.numpy()
spectro = librosa.core.stft(x)
origSpectroSize = spectro.shape
spectroSize = (512, 512)
scaledSpectro = sUtils.scaleSpectro(librosa.power_to_db(np.abs(spectro)), spectroSize, minAmp, maxAmp)
scaledPhase = sUtils.scaleSpectro(np.angle(spectro), spectroSize, -math.pi, math.pi)

print("scaledSpectro", scaledSpectro)
print ("scaledPhase", scaledPhase)
#scaledSpectro = scaledSpectro.data.numpy()
#scaledPhase = scaledPhase.data.numpy()

scaledSpectro [[113 166 177 ... 207 198 195]
 [103 157 143 ... 172 149 171]
 [121 175 177 ... 180 181 173]
 ...
 [ 18  37  70 ...  56  60 124]
 [ 10  65  45 ...  63  65 124]
 [  0  66  59 ...  65  46 124]]
scaledPhase [[  0  65 210 ...   9  85 134]
 [128 217  64 ... 226  98  39]
 [128 136 129 ... 244 205  16]
 ...
 [128 193 190 ... 236 159 104]
 [255 158  89 ...  23  19  63]
 [128 145  73 ...  14 253  21]]


In [4]:
# Get the power spectrogram from decibal version
'''backToSpectro = sUtils.unscaleSpectro(scaledSpectro[0], origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)'''
backToSpectro = librosa.core.db_to_power(sUtils.unscaleSpectro(scaledSpectro, origSpectroSize, minAmp, maxAmp))
backToPhase = sUtils.unscaleSpectro(scaledPhase, origSpectroSize, -math.pi, math.pi)
invStft = np.zeros(backToSpectro.shape, dtype=np.complex_)
for i in range(invStft.shape[0]):
    for j in range(invStft.shape[1]):
        invStft[i,j] = complex(backToSpectro[i,j]*math.cos(backToPhase[i,j]), backToSpectro[i,j]*math.sin(backToPhase[i,j]))
n = len(x)
y_hat = librosa.istft(invStft, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)

In [5]:
librosa.output.write_wav('scaledExample.wav', y_hat, sr)

In [5]:
scaledSpectro = np.expand_dims(scaledSpectro, 0).astype(np.float32)
scaledPhase = np.expand_dims(scaledPhase, 0).astype(np.float32)

In [6]:
modelMag = models.__dict__['resnet18']()
modelMag = torch.nn.DataParallel(modelMag).cuda()
modelPhase = models.__dict__['resnet18']()
modelPhase = torch.nn.DataParallel(modelPhase).cuda()

In [7]:
checkpoint_path = 'resnet18/checkpoints/checkpoint_mag_512.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
modelMag.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

checkpoint_path = 'resnet18/checkpoints/checkpoint_phase_512.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
modelPhase.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

modelMag = nn.Sequential(*list(modelMag.children())[:-3])
modelPhase = nn.Sequential(*list(modelPhase.children())[:-3])

=> loading checkpoint 'resnet18/checkpoints/checkpoint_mag_512.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/checkpoint_mag_512.pth.tar' (epoch: 200) (best_acc: 53.01668808120512)
=> loading checkpoint 'resnet18/checkpoints/checkpoint_phase_512.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/checkpoint_phase_512.pth.tar' (epoch: 200) (best_acc: 37.48395378690629)


In [8]:
print ("scaledSpectro.shape", scaledSpectro.shape)
dreamSpectro = dream(modelMag, scaledSpectro)
dreamSpectro = dreamSpectro[0,:]
print ("dreamSpectro")
print (dreamSpectro)

scaledSpectro.shape (1, 512, 512)
model after removing 0
(1, 95, 95)
ratio 138.41887
learning_rate_use 0.002889779427011364
imgBefore [[[1.13326546e+02 1.79969360e+02 1.88456650e+02 ... 1.90430298e+02
   2.01334457e+02 1.95563507e+02]
  [1.10432068e+02 1.85568695e+02 1.88608887e+02 ... 2.05143677e+02
   2.05335403e+02 1.96393753e+02]
  [1.03121315e+02 1.82095810e+02 1.92863251e+02 ... 2.00273193e+02
   2.07938934e+02 2.05669632e+02]
  ...
  [2.49802513e+01 5.94071541e+01 5.72945900e+01 ... 5.90360489e+01
   6.02893028e+01 1.24549232e+02]
  [2.12822456e+01 5.86843147e+01 5.72573166e+01 ... 5.81061249e+01
   5.98881645e+01 1.24359413e+02]
  [5.70076863e-13 5.92788582e+01 5.95432930e+01 ... 5.69415016e+01
   5.79042587e+01 1.24358330e+02]]]
imgAfter (1, 95, 95)
ratio 138.81886
learning_rate_use 0.0028814527910721393
imgBefore [[[1.13653091e+02 1.80487930e+02 1.88999680e+02 ... 1.90979019e+02
   2.01914597e+02 1.96127014e+02]
  [1.10750275e+02 1.86103409e+02 1.89152359e+02 ... 2.05734787e+

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


ratio 139.21887
learning_rate_use 0.0028731736872424883
imgBefore [[[1.1397964e+02 1.8100650e+02 1.8954271e+02 ... 1.9152774e+02
   2.0249474e+02 1.9669052e+02]
  [1.1106848e+02 1.8663812e+02 1.8969583e+02 ... 2.0632590e+02
   2.0651872e+02 1.9752556e+02]
  [1.0371560e+02 1.8314522e+02 1.9397470e+02 ... 2.0142734e+02
   2.0913727e+02 2.0685487e+02]
  ...
  [2.5124210e+01 5.9749516e+01 5.7624775e+01 ... 5.9376266e+01
   6.0636745e+01 1.2526699e+02]
  [2.1404892e+01 5.9022511e+01 5.7587288e+01 ... 5.8440987e+01
   6.0233295e+01 1.2507609e+02]
  [5.7336221e-13 5.9620480e+01 5.9886433e+01 ... 5.7269650e+01
   5.8237953e+01 1.2507499e+02]]]
imgAfter (1, 95, 95)
ratio 139.61887
learning_rate_use 0.002864942335909855
imgBefore [[[1.14306183e+02 1.81525070e+02 1.90085739e+02 ... 1.92076462e+02
   2.03074875e+02 1.97254028e+02]
  [1.11386688e+02 1.87172836e+02 1.90239304e+02 ... 2.06917007e+02
   2.07110382e+02 1.98091461e+02]
  [1.04012741e+02 1.83669922e+02 1.94530426e+02 ... 2.02004410e+02
 

imgBefore [[[1.3581290e+02 2.0180090e+02 2.1101682e+02 ... 2.5179913e+02
   2.4432529e+02 2.3436748e+02]
  [1.3749431e+02 2.0520815e+02 2.1029599e+02 ... 2.2840724e+02
   2.1953664e+02 2.0249117e+02]
  [1.3029822e+02 2.3063737e+02 2.1742117e+02 ... 2.4948830e+02
   2.4218289e+02 2.3092416e+02]
  ...
  [3.1820875e+01 6.7776886e+01 6.9678101e+01 ... 7.3146835e+01
   7.3655533e+01 1.4903474e+02]
  [1.1342292e+01 6.5520134e+01 6.3479790e+01 ... 7.0702110e+01
   7.6876137e+01 1.4903371e+02]
  [6.8319211e-13 6.6479378e+01 7.0436432e+01 ... 8.2698158e+01
   7.6458565e+01 1.4903368e+02]]]
imgAfter (1, 261, 261)
ratio 166.98552
learning_rate_use 0.0023954172877699888
imgBefore [[[1.3613823e+02 2.0228430e+02 2.1152229e+02 ... 2.5240230e+02
   2.4491055e+02 2.3492888e+02]
  [1.3782367e+02 2.0569971e+02 2.1079974e+02 ... 2.2895438e+02
   2.2006252e+02 2.0297621e+02]
  [1.3061034e+02 2.3118985e+02 2.1794199e+02 ... 2.5008592e+02
   2.4276302e+02 2.3147733e+02]
  ...
  [3.1897099e+01 6.7939240e+01 6

   7.7689209e+01 1.6655629e+02]]]
imgAfter (1, 512, 512)
ratio 185.60449
learning_rate_use 0.0021551202521322326
imgBefore [[[1.5210814e+02 2.1438640e+02 2.3069740e+02 ... 2.5554956e+02
   2.5554956e+02 2.5554956e+02]
  [1.4147116e+02 2.0481210e+02 1.9511041e+02 ... 2.3590855e+02
   2.1222369e+02 2.3521249e+02]
  [1.6028203e+02 2.2416359e+02 2.3140073e+02 ... 2.4590068e+02
   2.4588330e+02 2.3607007e+02]
  ...
  [2.1803566e+01 4.7060410e+01 8.5325584e+01 ... 8.3498543e+01
   9.2683083e+01 1.6691548e+02]
  [1.2184799e+01 7.5585587e+01 5.8748386e+01 ... 9.0895561e+01
   9.7888092e+01 1.6691525e+02]
  [1.7123564e-13 7.5903038e+01 7.2977341e+01 ... 9.3064690e+01
   7.7856636e+01 1.6691524e+02]]]
imgAfter (1, 512, 512)
out
[[[1.5210814e+02 2.1438640e+02 2.3069740e+02 ... 2.5500000e+02
   2.5500000e+02 2.5500000e+02]
  [1.4147116e+02 2.0481210e+02 1.9511041e+02 ... 2.3590855e+02
   2.1222369e+02 2.3521249e+02]
  [1.6028203e+02 2.2416359e+02 2.3140073e+02 ... 2.4590068e+02
   2.4588330e+02 2.

In [9]:
dreamPhase = dream(modelPhase, scaledPhase)
dreamPhase = dreamPhase[0,:]
print ("dreamPhase")
print (dreamPhase)

model after removing 0
(1, 95, 95)
ratio 127.53346
learning_rate_use 0.00313643174177465
imgBefore [[[  0.       112.94219  103.51669  ... 112.53818  119.23784  134.42029 ]
  [117.2762   127.44707  107.80599  ... 135.23929  135.76007   88.72853 ]
  [145.00134  138.18355  128.89813  ... 141.83861  132.84547  163.02147 ]
  ...
  [ 71.22379  131.49141  104.90429  ... 113.85504  142.97623  125.29005 ]
  [182.15425  135.27206  126.6608   ... 142.08302  132.46848  119.30477 ]
  [128.40146  128.95375  124.64797  ... 132.97455  166.11986   21.065865]]]
imgAfter (1, 95, 95)
ratio 127.933464
learning_rate_use 0.003126625257663255
imgBefore [[[  0.       113.29532  103.84035  ... 112.890045 119.61065  134.84058 ]
  [117.642876 127.84554  108.14306  ... 135.66212  136.18454   89.00595 ]
  [145.45471  138.6156   129.30115  ... 142.28209  133.26083  163.53117 ]
  ...
  [ 71.44648  131.90253  105.232285 ... 114.21102  143.42326  125.68178 ]
  [182.72379  135.695    127.056816 ... 142.52727  132.88266

ratio 149.94322
learning_rate_use 0.0026676764347344614
imgBefore [[[  0.        87.58984  163.6122   ... 160.75627  148.85098  157.95505 ]
  [143.35873  144.15378  112.1386   ... 176.05072  141.998     69.99884 ]
  [119.8223   123.697426 157.77406  ... 166.26122  152.73364  111.60028 ]
  ...
  [198.79736  146.914    141.64955  ... 134.60097  134.43846  128.64261 ]
  [252.93022  165.98454  150.03152  ... 139.96844  131.23582  152.87222 ]
  [150.88225  150.44693  120.05668  ... 173.32277  167.19366   24.754116]]]
imgAfter (1, 186, 186)
ratio 150.34285
learning_rate_use 0.0026605854599305034
imgBefore [[[  0.        87.82288  164.0475   ... 161.18398  149.24701  158.3753  ]
  [143.74016  144.53731  112.43696  ... 176.51912  142.3758    70.18508 ]
  [120.1411   124.026535 158.19383  ... 166.70357  153.14     111.8972  ]
  ...
  [199.32628  147.30489  142.02643  ... 134.95909  134.79614  128.98488 ]
  [253.60316  166.42616  150.4307   ... 140.34084  131.58499  153.27895 ]
  [151.28368  150

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


ratio 151.49245
learning_rate_use 0.0026403956645151207
imgBefore [[[  0.       110.6642    54.324303 ... 169.58627  137.5336   159.63622 ]
  [140.1115   153.03616  161.57321  ... 106.472115 159.73698   56.50201 ]
  [146.4077   156.55551   82.66526  ... 201.85097  116.53771   96.33132 ]
  ...
  [263.38846  131.72072  162.06667  ... 100.72291  166.9061   204.08943 ]
  [246.49806  190.78142  174.3587   ... 110.69883  139.33768  117.15768 ]
  [152.48813  159.73494  140.52626  ... 203.74704  141.97096   25.01758 ]]]
imgAfter (1, 261, 261)
ratio 151.87685
learning_rate_use 0.002633712838455921
imgBefore [[[  0.       110.95566   54.467377 ... 170.03291  137.89583  160.05666 ]
  [140.48051  153.43922  161.99875  ... 106.75253  160.15768   56.65082 ]
  [146.79329  156.96783   82.88298  ... 202.38258  116.84464   96.58503 ]
  ...
  [255.6716   132.06763  162.4935   ... 100.98818  167.34567  204.62694 ]
  [247.14726  191.28387  174.81792  ... 110.99038  139.70465  117.46624 ]
  [152.88974  160.

imgBefore [[[  0.        78.91462  233.45839  ...  49.614258 125.56856  179.50699 ]
  [145.61642  243.5034    91.77314  ... 255.6163   137.41121   72.41615 ]
  [155.47398  167.47165  162.8418   ... 255.6163   244.7365    43.825066]
  ...
  [170.91774  241.52968  238.53055  ... 255.6163   193.49902  132.48695 ]
  [255.6163   207.17433  135.59888  ...  55.4761    44.89348   81.360016]
  [171.46912  188.38301  115.5497   ...  45.205574 255.6163    28.131649]]]
imgAfter (1, 512, 512)
ratio 165.79488
learning_rate_use 0.002412619795089666
imgBefore [[[  0.        79.10501  234.02164  ...  49.73396  125.871506 179.94006 ]
  [145.96774  244.09088   91.99455  ... 255.61522  137.74274   72.590866]
  [155.84909  167.8757   163.23466  ... 255.61522  245.32695   43.930798]
  ...
  [171.3301   242.1124   239.10603  ... 255.61522  193.96587  132.8066  ]
  [255.61522  207.67416  135.92603  ...  55.609943  45.00179   81.556305]
  [171.88281  188.83751  115.828476 ...  45.314636 255.61522   28.19952 ]]

In [10]:
#Convert it back to 
'''backToSpectro = sUtils.unscaleSpectro(dreamSpectro, origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)'''
backToSpectro = librosa.core.db_to_power(sUtils.unscaleSpectro(dreamSpectro, origSpectroSize, minAmp, maxAmp))
backToPhase = sUtils.unscaleSpectro(dreamPhase, origSpectroSize, -math.pi, math.pi)
invStft = np.zeros(backToSpectro.shape, dtype=np.complex_)
for i in range(invStft.shape[0]):
    for j in range(invStft.shape[1]):
        invStft[i,j] = complex(backToSpectro[i,j]*math.cos(backToPhase[i,j]), backToSpectro[i,j]*math.sin(backToPhase[i,j]))
n = len(x)
y_hat = librosa.istft(invStft, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)

In [11]:
librosa.output.write_wav('dreamExample.wav', y_hat, sr)

## Noise Dream

In [13]:
noiseSpectro = np.random.random(spectroSize)*255
noisePhase = np.random.random(spectroSize)*2*math.pi - math.pi
backToNoiseSpectro = librosa.core.db_to_power(sUtils.unscaleSpectro(noiseSpectro, origSpectroSize, minAmp, maxAmp))
backToNoisePhase = sUtils.unscaleSpectro(noisePhase, origSpectroSize, -math.pi, math.pi)
invStftNoise = np.zeros(backToNoiseSpectro.shape, dtype=np.complex_)
for i in range(invStftNoise.shape[0]):
    for j in range(invStftNoise.shape[1]):
        invStftNoise[i,j] = complex(backToNoiseSpectro[i,j]*math.cos(backToNoisePhase[i,j]), backToNoiseSpectro[i,j]*math.sin(backToNoisePhase[i,j]))
n = len(x)
y_hat = librosa.istft(invStftNoise, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)


In [14]:
noiseSpectro = np.expand_dims(noiseSpectro, 0).astype(np.float32)
noisePhase = np.expand_dims(noisePhase, 0).astype(np.float32)

In [15]:
modelMag = models.__dict__['resnet18']()
modelMag = torch.nn.DataParallel(modelMag).cuda()
modelPhase = models.__dict__['resnet18']()
modelPhase = torch.nn.DataParallel(modelPhase).cuda()

In [16]:
checkpoint_path = 'resnet18/checkpoints/checkpoint_mag_512.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
modelMag.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

checkpoint_path = 'resnet18/checkpoints/checkpoint_phase_512.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
modelPhase.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

modelMag = nn.Sequential(*list(modelMag.children())[:-3])
modelPhase = nn.Sequential(*list(modelPhase.children())[:-3])

=> loading checkpoint 'resnet18/checkpoints/checkpoint_mag_512.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/checkpoint_mag_512.pth.tar' (epoch: 200) (best_acc: 53.01668808120512)
=> loading checkpoint 'resnet18/checkpoints/checkpoint_phase_512.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/checkpoint_phase_512.pth.tar' (epoch: 200) (best_acc: 37.48395378690629)


In [17]:
print ("noiseSpectro.shape", noiseSpectro.shape)
dreamNoiseSpectro = dream(modelMag, noiseSpectro)
dreamNoiseSpectro = dreamNoiseSpectro[0,:]
print ("dreamNoiseSpectro")
print (dreamNoiseSpectro)

noiseSpectro.shape (1, 512, 512)
model after removing 0
(1, 95, 95)
ratio 127.6472
learning_rate_use 0.0031336370494628707
imgBefore [[[128.53131  154.54538  136.96591  ... 111.44171  141.46027   31.008347]
  [173.86589  117.39202  132.38318  ... 132.49312  118.576225 131.20679 ]
  [140.55959  113.39884  114.78236  ... 134.68451  124.71725  134.77118 ]
  ...
  [107.9526   125.574554 128.99698  ... 112.7637   122.11603  130.97423 ]
  [147.3885   121.636986 119.88461  ... 120.62405  120.10815  145.6288  ]
  [219.77994  109.148796 183.69208  ... 125.434326 144.3368    85.69329 ]]]
imgAfter (1, 95, 95)
ratio 128.04721
learning_rate_use 0.0031238478201442333
imgBefore [[[128.93283  155.02815  137.39377  ... 111.78984  141.90216   31.105211]
  [174.40903  117.758736 132.79672  ... 132.90701  118.94664  131.61665 ]
  [140.99867  113.75308  115.14092  ... 135.10524  125.10684  135.19218 ]
  ...
  [108.289825 125.96683  129.39995  ... 113.11596  122.4975   131.38338 ]
  [147.84892  122.01696  1

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


[[[152.6342   162.43115  129.90735  ... 117.811676 181.1264    36.823174]
  [187.96944  155.78557  201.788    ... 199.99988  156.50607  171.71469 ]
  [220.1145   143.72166  133.21031  ... 186.73785  116.880936 183.11969 ]
  ...
  [160.96414  126.77275  102.91056  ... 188.26645  133.71262  140.51924 ]
  [233.56783  150.81769  159.93172  ... 179.55704  162.54646  189.93683 ]
  [255.67326  122.15106  115.92611  ... 220.22784  137.43068  101.76292 ]]]
imgAfter (1, 261, 261)
ratio 151.8949
learning_rate_use 0.002633399848753097
imgBefore [[[153.03615  162.8589   130.24945  ... 118.12192  181.60338   36.920143]
  [188.46443  156.19582  202.31938  ... 200.52655  156.91821  172.16689 ]
  [220.69415  144.10014  133.56111  ... 187.22961  117.18873  183.60191 ]
  ...
  [161.38803  127.1066   103.181564 ... 188.76222  134.06473  140.88928 ]
  [234.1829   151.21484  160.35287  ... 180.02988  162.97452  190.43701 ]
  [255.67152  122.47273  116.23139  ... 220.80779  137.79259  102.0309  ]]]
imgAfter 

imgAfter (1, 512, 512)
ratio 166.44316
learning_rate_use 0.002403222803333951
imgBefore [[[172.87202  255.61282   77.97982  ... 255.61282  242.7141    41.705555]
  [155.08034  255.61282   64.71519  ...  39.559574 115.836586 255.61282 ]
  [255.61282  126.1306   238.16797  ...  60.9024   255.61282  198.2524  ]
  ...
  [233.37256  255.61282  155.35359  ... 164.96793   71.5613   183.31639 ]
  [255.61282  196.39703   48.820107 ... 123.28593  197.89944  201.6981  ]
  [255.61282  166.38925  177.1774   ... 198.53978  137.67632  115.255684]]]
imgAfter (1, 512, 512)
ratio 166.72949
learning_rate_use 0.0023990956533962784
imgBefore [[[173.28676  255.61177   78.1669   ... 255.61177  243.29639   41.80561 ]
  [155.4524   255.61177   64.870445 ...  39.65448  116.11449  255.61177 ]
  [255.61177  126.4332   238.73935  ...  61.04851  255.61177  198.72803 ]
  ...
  [233.93243  255.61177  155.7263   ... 165.3637    71.73299  183.75618 ]
  [255.61177  196.86821   48.93723  ... 123.5817   198.37422  202.181

In [18]:
dreamNoisePhase = dream(modelPhase, noisePhase)
dreamNoisePhase = dreamNoisePhase[0,:]
print ("dreamNoisePhase")
print (dreamNoisePhase)

model after removing 0
(1, 95, 95)
ratio 0.24187262
learning_rate_use 1.6537630183521888
imgBefore [[[ 6.504586   -0.31947532 -2.8872075  ... -1.7041585   0.50873375
   -4.4949207 ]
  [-0.8511997  -0.113451    0.06238725 ... -0.01793505  0.25807914
   -1.7832274 ]
  [-2.2808824  -0.57067025 -0.17040668 ...  0.96174383  0.7244939
   -0.12971643]
  ...
  [ 2.0055025  -0.09573261  1.3755572  ... -1.0921189   0.12407727
    2.9803495 ]
  [-1.304876    0.3088514   1.3044157  ...  0.7466278  -0.32138744
    0.93430626]
  [-3.3410537  -3.263791    1.0853145  ... -3.8376217  -2.1918952
    0.01739137]]]
imgAfter (1, 95, 95)
ratio 0.32063594
learning_rate_use 1.247520768430777
imgBefore [[[14.619193    0.          0.         ...  0.          1.1433897
    0.        ]
  [ 0.          0.          0.14021665 ...  0.          0.58003825
    0.        ]
  [ 0.          0.          0.         ...  2.1615393   1.6283152
    0.        ]
  ...
  [ 4.5074086   0.          3.0915933  ...  0.          0.27

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


imgBefore [[[2.58949158e+02 2.42381119e+02 1.67605774e+02 ... 2.60881767e+01
   1.74440975e+01 0.00000000e+00]
  [2.45453491e+02 1.77303528e+02 1.09873230e+02 ... 2.14814911e+01
   1.46149149e+01 1.38466030e-01]
  [1.67649307e+02 1.11219666e+02 6.42886887e+01 ... 1.99007835e+01
   1.28647041e+01 2.57319856e+00]
  ...
  [1.28439646e+01 1.59725246e+01 2.02204018e+01 ... 2.54238873e+01
   3.86097450e+01 6.35539055e+01]
  [2.19465113e+00 5.79409504e+00 1.31024046e+01 ... 1.19645634e+01
   1.78012657e+01 2.76758690e+01]
  [0.00000000e+00 1.51927626e+00 5.42554045e+00 ... 1.43737984e+00
   1.51009417e+00 1.42400289e+00]]]
imgAfter (1, 261, 261)
ratio 26.227276
learning_rate_use 0.015251298011744322
imgBefore [[[2.5888907e+02 2.4607774e+02 1.7016199e+02 ... 2.6486055e+01
   1.7710142e+01 0.0000000e+00]
  [2.4919698e+02 1.8000763e+02 1.1154894e+02 ... 2.1809113e+01
   1.4837811e+01 1.4057782e-01]
  [1.7020618e+02 1.1291591e+02 6.5269173e+01 ... 2.0204296e+01
   1.3060907e+01 2.6124432e+00]
  .

ratio 45.918102
learning_rate_use 0.008711161399849052
imgBefore [[[2.57221344e+02 2.57221344e+02 2.57221344e+02 ... 3.10261745e+01
   1.47508116e+01 0.00000000e+00]
  [2.57221344e+02 2.57221344e+02 2.57221344e+02 ... 2.44238319e+01
   1.82968712e+01 2.80502057e+00]
  [2.57221344e+02 2.57221344e+02 2.57221344e+02 ... 2.37723961e+01
   1.35987053e+01 0.00000000e+00]
  ...
  [8.90745640e+00 1.19933462e+01 1.47549715e+01 ... 3.45015335e+01
   4.19453163e+01 5.19939461e+01]
  [1.95066649e-02 4.72951460e+00 4.85691643e+00 ... 1.89145241e+01
   2.39433746e+01 2.58217316e+01]
  [0.00000000e+00 5.77977419e+00 1.32167614e+00 ... 1.43199766e+00
   6.08788395e+00 2.53639269e+00]]]
imgAfter (1, 512, 512)
ratio 46.312096
learning_rate_use 0.008637052468782429
imgBefore [[[2.5720245e+02 2.5720245e+02 2.5720245e+02 ... 3.1294149e+01
   1.4878215e+01 0.0000000e+00]
  [2.5720245e+02 2.5720245e+02 2.5720245e+02 ... 2.4634783e+01
   1.8454903e+01 2.8292477e+00]
  [2.5720245e+02 2.5720245e+02 2.5720245e+0

In [19]:
backToSpectro = librosa.core.db_to_power(sUtils.unscaleSpectro(dreamNoiseSpectro, origSpectroSize, minAmp, maxAmp))
backToPhase = sUtils.unscaleSpectro(dreamNoisePhase, origSpectroSize, -math.pi, math.pi)
invStftNoiseDream = np.zeros(backToSpectro.shape, dtype=np.complex_)
for i in range(invStftNoiseDream.shape[0]):
    for j in range(invStftNoiseDream.shape[1]):
        invStftNoiseDream[i,j] = complex(backToSpectro[i,j]*math.cos(backToPhase[i,j]), backToSpectro[i,j]*math.sin(backToPhase[i,j]))
n = len(x)
y_hat = librosa.istft(invStftNoiseDream, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)

In [20]:
librosa.output.write_wav('dreamNoiseExample.wav', y_hat, sr)

## Control The Dream

In [26]:
#spectroSize = 224
otherTrackId = 821
'''otherSpectro, otherPhase, otherOrigSpectroSize = sUtils.loadSpectro(otherTrackId, spectroSize, minAmp, maxAmp)
otherSpectro = otherSpectro.data.numpy()'''
audioFilename = audioDirectory + "000/000821.mp3"
x, sr = librosa.load(audioFilename, sr=None, mono=True, duration = 10, offset = 0)

otherSpectro = librosa.core.stft(x)
origSpectroSize = spectro.shape
spectroSize = (512, 512)
otherScaledSpectro = sUtils.scaleSpectro(librosa.power_to_db(np.abs(otherSpectro)), spectroSize, minAmp, maxAmp)
otherScaledPhase = sUtils.scaleSpectro(np.angle(otherSpectro), spectroSize, -math.pi, math.pi)

start, end = 0, 10
ipd.Audio(data=x[start*sr:end*sr], rate=sr)

In [27]:
modelMag = models.__dict__['resnet18']()
modelMag = torch.nn.DataParallel(modelMag).cuda()
modelPhase = models.__dict__['resnet18']()
modelPhase = torch.nn.DataParallel(modelPhase).cuda()

checkpoint_path = 'resnet18/checkpoints/checkpoint_mag_512.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
modelMag.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

checkpoint_path = 'resnet18/checkpoints/checkpoint_phase_512.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
modelPhase.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

modelMag = nn.Sequential(*list(modelMag.children())[:-3])
modelPhase = nn.Sequential(*list(modelPhase.children())[:-3])

=> loading checkpoint 'resnet18/checkpoints/checkpoint_mag_512.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/checkpoint_mag_512.pth.tar' (epoch: 200) (best_acc: 53.01668808120512)
=> loading checkpoint 'resnet18/checkpoints/checkpoint_phase_512.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/checkpoint_phase_512.pth.tar' (epoch: 200) (best_acc: 37.48395378690629)


In [28]:
otherScaledSpectro = torch.from_numpy(otherScaledSpectro).type(torch.DoubleTensor)
otherScaledSpectro = Variable(otherScaledSpectro).unsqueeze(0)

otherScaledPhase = torch.from_numpy(otherScaledPhase).type(torch.DoubleTensor)
otherScaledPhase = Variable(otherScaledPhase).unsqueeze(0)

control_features_mag = modelMag.forward(otherScaledSpectro)
control_features_phase = modelPhase.forward(otherScaledPhase)
control_features_mag = control_features_mag.data.numpy()
control_features_phase = control_features_phase.data.numpy()

In [29]:
def objective_guide(dst, guide_features):
    x = dst.data[0].cpu().numpy().copy()
    #print ("guide_features", guide_features.shape)
    y = guide_features
    w, h = x.shape
    ch = 1
    x = x.reshape(ch,-1)
    y = y.reshape(ch,-1)
    print ("shape of x", x.shape)
    print ("shape of y", y.shape)
    #A = x.T.dot(y) # compute the matrix of dot-products with guide features
    #A = torch.mm(torch.from_numpy(x.T).type(torch.DoubleTensor), torch.from_numpy(y).type(torch.DoubleTensor)).numpy()
    #A = np.zeros((x.shape[1],y.shape[1]))
    maxColumnIndices = []
    batchSize = 9000
    numBatches = x.shape[1]//batchSize
    for batchNum in range(numBatches):
        start = batchNum*batchSize
        end = start+batchSize
        if batchNum == numBatches-1:
            end = x.shape[1]
        #print ("x portion shape", (x[0,start:end].T).shape)
        #print ("y portion shape", (y).shape)
        prod = np.dot((x[0,start:end].T).reshape(-1,1), y)
        argMax = prod.argmax(1)
        for val in list(argMax):
            maxColumnIndices.append(val)
        del prod
    '''for i in range(x.shape[1]):
        row = np.dot(x[0,i],y[0,:])
        maxColumnIndices.append(row.argmax())
        del row
        #A[i,:] = np.dot(x[0,i],y[0,:])'''
    #print ("shape of A", A.shape)
    #result = y[:,A.argmax(1)] # select ones that match best
    #print ("shape of result", result.shape)
    result = y[:,maxColumnIndices]
    print ("shape of result", result.shape)
    if torch.cuda.is_available():
        result = torch.Tensor(np.array([result.reshape(ch, w, h)], dtype=np.float)).cuda()
    else:
        result = torch.Tensor(np.array([result.reshape(ch, w, h)], dtype=np.float))
    return result

In [30]:
hopRockDreamSpectro = dream(modelMag, scaledSpectro, control=control_features_mag, distance=objective_guide, layerNumber=3)
print(hopRockDreamSpectro)

model after removing 0
(1, 95, 95)
shape of x (1, 9025)
shape of y 

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


(1, 262144)
shape of result (1, 9025)
ratio 

/home/iaakhter/cs532l/DreamingInMusic/deepDream.py:48: UserWarning: other is not broadcastable to self, but they have the same number of elements.  Falling back to deprecated pointwise behavior.
  img_variable.data.add_(img_variable.grad.data * learning_rate_use)


254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[113.4      179.85078  188.31361  ... 190.28157  201.15431  195.4     ]
  [110.51386  185.43398  188.46541  ... 204.95256  205.14374  196.22784 ]
  [103.224174 181.9711   192.70752  ... 200.09612  207.73976  205.477   ]
  ...
  [ 25.308271  59.635975  57.5295   ...  59.26594   60.515583 124.590355]
  [ 21.620922  58.91522   57.492332 ...  58.338696  60.1156   124.40108 ]
  [  0.4       59.50805   59.771725 ...  57.17743   58.137413 124.4     ]]]
imgAfter (1, 95, 95)
shape of x (1, 9025)
shape of y (1, 262144)
shape of result (1, 9025)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[113.8      180.25078  188.71361  ... 190.68156  201.5543   195.79999 ]
  [110.913864 185.83397  188.8654   ... 205.35255  205.54373  196.62784 ]
  [103.624176 182.3711   193.10751  ... 200.49611  208.13976  205.877   ]
  ...
  [ 25.708271  60.035976  57.9295   ...  59.665943  60.915585 124.99036 ]
  [ 22.020922  59.31522   57.892334 .

...

shape of y (1, 262144)
shape of result (1, 34596)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[135.79994  196.76984  203.5003   ... 232.95995  229.39175  217.79965 ]
  [134.98706  205.08226  203.01257  ... 233.04135  214.9859   198.75537 ]
  [124.46328  221.60689  217.677    ... 234.17178  223.39034  221.72107 ]
  ...
  [ 51.939957  81.78547   83.79357  ...  82.517334  80.711334 146.79973 ]
  [ 39.69172   80.201355  84.34088  ...  80.582344  80.76417  146.79973 ]
  [ 22.799988  82.678856  83.366196 ...  75.41546   85.57776  146.79973 ]]]
imgAfter (1, 186, 186)
shape of x (1, 34596)
shape of y (1, 262144)
shape of result (1, 34596)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[136.19994  197.16983  203.9003   ... 233.35994  229.79175  218.19965 ]
  [135.38705  205.48225  203.41257  ... 233.44135  215.3859   199.15536 ]
  [124.86328  222.00688  218.077    ... 234.57178  223.79033  222.12106 ]
  ...
  [ 52.33996   82.18547   84.19357  ...  82.917336 

shape of y (1, 262144)
shape of result (1, 68121)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[141.79985  200.5728   205.99194  ... 239.51495  232.58034  223.79956 ]
  [143.68446  203.59358  204.85715  ... 216.97054  209.15352  193.65341 ]
  [137.03069  228.13416  211.3115   ... 237.44109  231.13562  221.03802 ]
  ...
  [ 56.792366  88.32094   87.98944  ...  87.93372   85.052246 152.79964 ]
  [ 38.12312   86.705055  82.12394  ...  85.6105    88.17423  152.79964 ]
  [ 28.799982  88.36545   89.13856  ...  97.33852   87.64994  152.79964 ]]]
imgAfter (1, 261, 261)
shape of x (1, 68121)
shape of y (1, 262144)
shape of result (1, 68121)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[142.19984  200.9728   206.39194  ... 239.91495  232.98033  224.19955 ]
  [144.08446  203.99358  205.25714  ... 217.37053  209.55351  194.0534  ]
  [137.43068  228.53415  211.71149  ... 237.84108  231.53561  221.43802 ]
  ...
  [ 57.192368  88.72094   88.38944  ...  88.333725 

shape of y (1, 262144)
shape of result (1, 133956)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[147.39977  204.79967  208.19962  ... 241.39948  235.99948  229.39948 ]
  [144.59976  195.55968  203.31961  ... 210.23947  201.55948  206.19948 ]
  [156.1998   224.9197   224.35962  ... 232.79947  226.51947  188.99948 ]
  ...
  [ 38.00007   88.92009   97.6801   ...  91.84001   94.39986  158.39955 ]
  [ 47.60004   88.68008   97.4001   ...  90.76001   96.27986  158.39955 ]
  [ 34.399986  97.60006   88.6001   ... 101.000015  87.999855 158.39955 ]]]
imgAfter (1, 366, 366)
shape of x (1, 133956)
shape of y (1, 262144)
shape of result (1, 133956)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[147.79976  205.19966  208.59961  ... 241.79947  236.39948  229.79947 ]
  [144.99976  195.95967  203.7196   ... 210.63947  201.95947  206.59947 ]
  [156.5998   225.31969  224.75961  ... 233.19946  226.91946  189.39948 ]
  ...
  [ 38.40007   89.32009   98.0801   ...  92.2400

shape of result (1, 133956)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[152.99968  210.39958  213.79953  ... 246.99939  241.5994   234.99939 ]
  [150.19968  201.15959  208.91953  ... 215.83939  207.1594   211.7994  ]
  [161.79971  230.5196   229.95953  ... 238.39938  232.11938  194.5994  ]
  ...
  [ 43.60009   94.52011  103.28012  ...  97.44003   99.99988  163.99947 ]
  [ 53.20006   94.2801   103.00012  ...  96.36003  101.87988  163.99947 ]
  [ 40.000008 103.20008   94.20012  ... 106.60004   93.59988  163.99947 ]]]
imgAfter (1, 366, 366)
(1, 512, 512)
shape of x (1, 262144)
shape of y (1, 262144)
shape of result (1, 262144)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[153.39967  206.39961  217.39955  ... 247.39938  238.39938  235.39938 ]
  [143.39967  197.39961  183.39955  ... 212.39938  189.39938  211.39938 ]
  [161.39969  215.39961  217.39957  ... 220.39938  221.39938  213.39938 ]
  ...
  [ 58.400074  77.40009  110.40011  ...  96.39995  100.39

shape of result (1, 262144)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[158.5996   211.59953  222.59947  ... 252.5993   243.5993   240.5993  ]
  [148.5996   202.59953  188.59947  ... 217.5993   194.5993   216.5993  ]
  [166.59961  220.59953  222.59949  ... 225.5993   226.5993   218.5993  ]
  ...
  [ 63.600094  82.60011  115.60013  ... 101.59997  105.599785 169.59938 ]
  [ 55.600067 110.6001    90.60013  ... 108.59997  110.599785 169.59938 ]
  [ 45.60003  111.60008  104.60011  ... 110.59997   91.59978  169.59938 ]]]
imgAfter (1, 512, 512)
shape of x (1, 262144)
shape of y (1, 262144)
shape of result (1, 262144)
ratio 254.0
learning_rate_use 0.0015748031496062994
imgBefore [[[158.99959  211.99953  222.99947  ... 252.9993   243.9993   240.9993  ]
  [148.99959  202.99953  188.99947  ... 217.9993   194.9993   216.9993  ]
  [166.9996   220.99953  222.99948  ... 225.9993   226.9993   218.9993  ]
  ...
  [ 64.00009   83.000114 116.00013  ... 101.99997  105.99979  169.99937

In [31]:
hopRockDreamPhase = dream(modelPhase, scaledPhase, control=control_features_phase, distance=objective_guide, layerNumber=3)
print(hopRockDreamPhase)

model after removing 0
(1, 95, 95)
shape of x (1, 9025)


/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


shape of y (1, 262144)
shape of result (1, 9025)
ratio 254.98593
learning_rate_use 0.0015687139984912714
imgBefore [[[  0.2007954 112.98909   103.59306   ... 112.586334  119.26505
   134.40002  ]
  [117.30955   127.448616  107.86895   ... 135.21648   135.73563
    88.851135 ]
  [144.948     138.15152   128.89514   ... 141.79515   132.83014
   162.91179  ]
  ...
  [ 71.40113   131.48032   104.97632   ... 113.899086  142.92921
   125.29834  ]
  [181.98474   135.24915   126.6648    ... 142.0388    132.45432
   119.33177  ]
  [128.40002   128.95059   124.65827   ... 132.95882   166.00049
    21.400023 ]]]
imgAfter (1, 95, 95)
shape of x (1, 9025)
shape of y 

/home/iaakhter/cs532l/DreamingInMusic/deepDream.py:48: UserWarning: other is not broadcastable to self, but they have the same number of elements.  Falling back to deprecated pointwise behavior.
  img_variable.data.add_(img_variable.grad.data * learning_rate_use)


(1, 262144)
shape of result (1, 9025)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[  0.6007954 113.38909   103.993065  ... 112.986336  119.665054
   134.80002  ]
  [117.70955   127.84862   108.26895   ... 135.61647   136.13562
    89.25114  ]
  [145.34799   138.55151   129.29514   ... 142.19514   133.23013
   163.31178  ]
  ...
  [ 71.80113   131.88031   105.37632   ... 114.29909   143.32921
   125.69834  ]
  [182.38474   135.64914   127.064804  ... 142.4388    132.85431
   119.73177  ]
  [128.80002   129.35059   125.05827   ... 133.35881   166.40048
    21.800022 ]]]
imgAfter (1, 95, 95)
shape of x (1, 9025)
shape of y (1, 262144)
shape of result (1, 9025)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[  1.0007954 113.78909   104.39307   ... 113.38634   120.065056
   135.20001  ]
  [118.10955   128.24861   108.66895   ... 136.01646   136.53561
    89.65114  ]
  [145.74799   138.9515    129.69513   ... 142.59514   133.63013
   163.71178  ]
  ...
  

...

shape of y (1, 262144)
shape of result (1, 34596)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 22.600782  98.20229  166.1687   ... 161.32814  148.74487  156.79968 ]
  [150.70189  148.3216   115.769806 ... 175.0139   143.35168   77.045944]
  [123.452156 125.96593  157.94923  ... 165.00357  153.59393  116.80523 ]
  ...
  [191.80408  144.97792  141.16222  ... 134.65854  135.68396  131.72487 ]
  [243.39615  163.44286  149.06978  ... 139.41844  133.9983   158.44144 ]
  [150.79968  150.86252  121.31608  ... 169.42755  169.62056   43.800056]]]
imgAfter (1, 186, 186)
shape of x (1, 34596)
shape of y (1, 262144)
shape of result (1, 34596)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 23.000782  98.602295 166.5687   ... 161.72813  149.14487  157.19968 ]
  [151.10188  148.72159  116.16981  ... 175.4139   143.75168   77.445946]
  [123.85216  126.36593  158.34923  ... 165.40356  153.99393  117.20523 ]
  ...
  [192.20407  145.37791  141.56221  ... 135.05853  

shape of y (1, 262144)
shape of result (1, 68121)
ratio 255.00002
learning_rate_use 0.001568627357116259
imgBefore [[[ 28.200777 129.54594   66.02958  ... 173.69203  141.1535   162.3996  ]
  [156.27264  164.94832  170.6123   ... 110.84485  165.89285   65.873   ]
  [156.3294   164.72531   89.838326 ... 205.84637  123.41956  107.24619 ]
  ...
  [255.4      131.48096  164.37743  ... 106.08163  173.79701  212.53056 ]
  [242.85728  191.28183  177.16827  ... 115.74701  148.12416  130.98064 ]
  [156.3996   163.98424  145.43048  ... 207.20735  153.41132   49.400078]]]
imgAfter (1, 261, 261)
shape of x (1, 68121)
shape of y (1, 262144)
shape of result (1, 68121)
ratio 255.00002
learning_rate_use 0.001568627357116259
imgBefore [[[ 28.600777 129.94594   66.42958  ... 174.09203  141.5535   162.79959 ]
  [156.67264  165.34831  171.0123   ... 111.24485  166.29285   66.273   ]
  [156.7294   165.1253    90.23833  ... 206.24637  123.819565 107.646194]
  ...
  [255.4      131.88095  164.77742  ... 106.4

shape of result (1, 133956)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 33.80078  156.85205  103.09693  ... 232.59961   88.599594 167.99951 ]
  [161.8519   180.65     161.0433   ... 135.03967  211.75967   63.79983 ]
  [161.89667  169.84322  163.58646  ...  98.959755 197.6398    82.799995]
  ...
  [255.4      175.8733   250.87955  ...  89.51976  228.5997   170.79976 ]
  [238.19951  188.95953  192.19955  ... 168.75969  122.27977  113.3999  ]
  [161.99951  150.19952  198.19957  ... 111.19968  191.3998    55.0001  ]]]
imgAfter (1, 366, 366)
shape of x (1, 133956)
shape of y (1, 262144)
shape of result (1, 133956)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 34.200783 157.25204  103.49693  ... 232.9996    88.999596 168.3995  ]
  [162.25189  181.04999  161.4433   ... 135.43967  212.15967   64.19983 ]
  [162.29666  170.24321  163.98645  ...  99.35976  198.0398    83.2     ]
  ...
  [255.4      176.2733   251.27954  ...  89.91976  228.9997   171.19975

shape of x (1, 133956)
shape of y (1, 262144)
shape of result (1, 133956)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 39.400803 162.45197  108.69695  ... 238.19952   94.199615 173.59943 ]
  [167.45181  186.24991  166.64322  ... 140.63959  217.35959   69.39985 ]
  [167.49658  175.44313  169.18637  ... 104.55978  203.23972   88.40002 ]
  ...
  [255.4      181.47322  255.4      ...  95.11978  234.19962  176.39967 ]
  [243.79942  194.55945  197.79947  ... 174.3596   127.87979  118.99992 ]
  [167.59943  155.79944  203.79948  ... 116.7997   196.99971   60.60012 ]]]
imgAfter (1, 366, 366)
shape of x (1, 133956)
shape of y (1, 262144)
shape of result (1, 133956)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 39.800804 162.85196  109.096954 ... 238.59952   94.59962  173.99942 ]
  [167.8518   186.6499   167.04321  ... 141.03958  217.75958   69.79985 ]
  [167.89658  175.84312  169.58636  ... 104.95978  203.63971   88.80002 ]
  ...
  [255.4      181.87321  

shape of y (1, 262144)
shape of result (1, 262144)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 45.000824 110.03736  255.07117  ...  54.199593 130.19954  179.19934 ]
  [173.03716  255.4      109.094795 ... 255.4      143.19955   84.199745]
  [173.07092  181.09459  174.11649  ... 255.4      250.19965   61.199944]
  ...
  [166.94244  236.16487  234.65672  ... 255.4      204.19966  149.19974 ]
  [255.4      203.19936  134.19937  ...  68.19972   64.199844 108.200005]
  [173.19934  190.19936  118.19947  ...  59.199726 255.4       66.20014 ]]]
imgAfter (1, 512, 512)
shape of x (1, 262144)
shape of y (1, 262144)
shape of result (1, 262144)
ratio 255.0
learning_rate_use 0.0015686274509803923
imgBefore [[[ 45.400826 110.43736  255.4      ...  54.599594 130.59953  179.59933 ]
  [173.43715  255.4      109.4948   ... 255.4      143.59955   84.59975 ]
  [173.47092  181.49458  174.51648  ... 255.4      250.59964   61.599945]
  ...
  [167.34244  236.56487  235.05672  ... 255.4   

In [32]:
'''hopRockDreamSpectro = hopRockDreamSpectro[0,:]
#Convert it back to 
backToSpectro = sUtils.unscaleSpectro(hopRockDreamSpectro, origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)'''
hopRockDreamSpectro = hopRockDreamSpectro[0,:]
hopRockDreamPhase = hopRockDreamPhase[0,:]

backToSpectro = librosa.core.db_to_power(sUtils.unscaleSpectro(hopRockDreamSpectro, origSpectroSize, minAmp, maxAmp))
backToPhase = sUtils.unscaleSpectro(hopRockDreamPhase, origSpectroSize, -math.pi, math.pi)
invStft = np.zeros(backToSpectro.shape, dtype=np.complex_)
for i in range(invStft.shape[0]):
    for j in range(invStft.shape[1]):
        invStft[i,j] = complex(backToSpectro[i,j]*math.cos(backToPhase[i,j]), backToSpectro[i,j]*math.sin(backToPhase[i,j]))
n = len(x)
y_hat = librosa.istft(invStft, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)


In [33]:
librosa.output.write_wav('dreamExampleControl.wav', y_hat, sr)